In [1]:
import numpy as np
from numpy import diff
from numpy import sum
from random import randint
import math
import time

np.__version__

'1.26.4'

In [2]:
from enum import Enum

class Game_Moment(Enum):
    SECOS_1 = 1
    DADOS_1 = 2
    SECOS_2 = 3
    DADOS_2 = 4
    TABELA = 5
    FIM = 6

In [3]:
class Yan:
    def __init__(self):
        # iniciar a coluna da desordem com -1 para indicar que as celulas estão vazias
        self.desordem = {"1": -1, "2": -1, "3": -1, "4": -1, "5": -1, "6": -1, "q": -1, "f": -1, "s+": -1, "s-": -1, "x+": -1, "x-": -1, "y": -1}
        self.yangame = "YanGame"
        self.dices = [0,0,0,0,0]
        self.current_state = Game_Moment.SECOS_1
        self.new_dice = list()
        self.marcado_em = ""
        self.over_minimum = False
        self.is_ended = False
        self.game_play = []
        self.next_state = self.get_game_state()
        self.reward = 0
        

        # self.action_size = self.row_count * self.column_count
    
    def check_consecutive(self, l):
        n = len(l) - 1
        return sum(diff(sorted(l)) == 1) >= n


    def roll_dice(self, n):
        rolls = list()
        for i in range(n):
            rolls.append(randint(1, 6))
        rolls.sort()
        self.game_play.append("você rolou:                          " + str(rolls))
        return rolls


    def get_game_state(self):
        state = [self.current_state]
        for die in self.dices:
            state.append(die)
        for item in self.desordem:
            state.append(self.desordem[item])
        return state
        
    def set_state(self, state):
        self.current_state = state[0]
        index = 1
        for die in range(len(self.dices)):
            self.dices[die] = state[index]
            index += 1

        index = 6
        for item in self.desordem:
            self.desordem[item] = state[index]
            index += 1

        return self.get_game_state()


    # onde é possivel anotar o resultado dos dados
    def get_empty_cells(self, state):
        self.set_state(state)
        avaiable_list = {}
        for item in self.desordem:
            if self.desordem[item] == -1:
                avaiable_list[item] = self.desordem[item]
        return avaiable_list
    
    def get_number_of_actions(self, state):
        if state[0] == Game_Moment.TABELA:
            # se estivermos na tabela, retornamos quantidade de celulas em branco
            return len(self.get_empty_cells(state))
        elif state[0] == Game_Moment.SECOS_1 or state[0] == Game_Moment.SECOS_2:
            #se tivermos no SECO retornamos binário "marcar/ não marcar"
            return 2
        else:
            # se estivermos nos dados retornamos 31 combinações de dados
            return 31


    def do_the_reroll(self, n_dices):
        dices_to_reroll = '{0:05b}'.format(int(n_dices))
        self.game_play.append("dados a serem rolados novamente:     " + dices_to_reroll)
        for index in range(len(str(dices_to_reroll))):
            if dices_to_reroll[index] == "1":
                self.dices[index] = self.roll_dice(1)[0]

        self.dices.sort()
        self.game_play.append("seus dados ficaram assim:            " + str(self.dices))
        dice_set = set(self.dices)
        n_single = len(dice_set)
        # return (6 - n_single) * 3
        return 0


    def reset(self):
        self.game_play = []
        self.game_play.append("Jogo iniciado")
        self.desordem = {"1": -1, "2": -1, "3": -1, "4": -1, "5": -1, "6": -1, "q": -1, "f": -1, "s+": -1, "s-": -1,
                         "x+": -1, "x-": -1,
                         "y": -1}
        self.current_state = Game_Moment.SECOS_1
        self.dices = self.roll_dice(5)
        self.dices.sort()
        self.is_ended = False

        return self.get_game_state()
    

    def get_initial_state(self):
        return self.reset()
    

    def get_valid_moves(self, state):
        game_state = state[0]       
        if game_state == Game_Moment.TABELA:
            # se estivermos na tabela, retornamos quantidade de celulas em branco
            return np.ones(len(self.get_empty_cells(state)))
        elif game_state == Game_Moment.SECOS_1 or game_state == Game_Moment.SECOS_2:
            #se tivermos no SECO retornamos binário "marcar/ não marcar"
            return np.ones(2)
        else:
            # se estivermos nos dados retornamos 31 combinações de dados
            return np.ones(31)
        # return self.get_number_of_actions()
        # return (state.reshape(-1) == 0).astype(np.uint8)
    

    def set_cell_value(self, cell: str):
        
        self.game_play.append("você marcou                          " + str(self.dices) + " em " + cell)
        self.game_play.append("\n")
        
        # self.marcado_em = 
        # print(self.marcado_em)
        points = 0

        match cell:
            case "1":
                points = self.dices.count(1)
                self.desordem["1"] = points
                return points
                
            case "2":
                points = self.dices.count(2) *2
                self.desordem["2"] = points
                return points
            case "3":
                points = self.dices.count(3) * 3
                self.desordem["3"] = points
                return points
            case "4":
                points = self.dices.count(4) * 4
                self.desordem["4"] = points
                return points
            case "5":
                points = self.dices.count(5) * 5
                self.desordem["5"] = points
                return points
            case "6":
                points = self.dices.count(6) * 6
                self.desordem["6"] = points
                return points
            case "y":
                if self.dices[0] == self.dices[4]:
                    self.desordem["y"] = sum(self.dices) + 50
                    return sum(self.dices) + 50
                else:
                    self.desordem["y"] = 0
                    return 0
            case "q":
                if self.dices[0] == self.dices[3]:
                    self.desordem["q"] = sum(self.dices[:4]) + 30
                    return sum(self.dices[:4]) + 30
                elif self.dices[1] == self.dices[4]:
                    self.desordem["q"] = sum(self.dices[1:]) + 30
                    return sum(self.dices[1:]) + 30
                else:
                    self.desordem["q"] = 0
                    return 0
            case "f":
                if (self.dices[0] == self.dices[2] and self.dices[3] == self.dices[4]) or (
                        self.dices[0] == self.dices[1] and self.dices[2] == self.dices[4]):
                    self.desordem["f"] = sum(self.dices) + 20
                    return sum(self.dices) + 20
 
                else:
                    self.desordem["f"] = 0
                    return 0
            case "s+":
                if self.check_consecutive(self.dices) and self.dices[0] == 2:
                    self.desordem["s+"] = 60
                    return 60
                else:
                    self.desordem["s+"] = 0
                    return 0
            case "s-":
                if self.check_consecutive( self.dices) and self.dices[0] == 1:
                    self.desordem["s-"] = 50
                    return 50
                else:
                    self.desordem["s-"] = 0
                    return 0
            case "x+":
                if (sum(self.dices) > self.desordem["x-"]) or self.desordem["x-"] == -1:
                    self.desordem["x+"] = sum(self.dices)
                    return sum(self.dices)
                else:
                    self.desordem["x+"] = 0
                return 0
            case "x-":
                if (sum(self.dices) < self.desordem["x+"]) or self.desordem["x+"] == -1:
                    self.desordem["x-"] = sum(self.dices)
                    return sum(self.dices)
                else:
                    self.desordem["x-"] = 0
                return 0
            

    def get_next_state(self, state, action):
        self.set_state(state)
        action = int(action)
        game_moment = state[0]       
        if game_moment == Game_Moment.SECOS_1:
            if action:
                self.game_play.append("você escolheu marcar")
                self.current_state = Game_Moment.TABELA

            else:
                self.game_play.append("você escolheu jogar novamente")
                self.current_state = Game_Moment.DADOS_1

            self.reward = 0
            return (self.get_game_state())
        
        elif game_moment == Game_Moment.DADOS_1:
            self.reward = self.do_the_reroll(n_dices=(int(action)+1))
            self.current_state = Game_Moment.SECOS_2
            return (self.get_game_state())
            return (self.get_game_state(), self.reward, self.is_ended)
        
        elif game_moment == Game_Moment.SECOS_2:
            if action:
                self.game_play.append("você escolheu marcar")
                self.current_state = Game_Moment.TABELA
            else:
                self.game_play.append("você escolheu jogar novamente")
                self.current_state = Game_Moment.DADOS_2

            self.reward = 0
            return (self.get_game_state())
            return (self.get_game_state(), self.reward, self.is_ended)

        elif game_moment == Game_Moment.DADOS_2:
            self.reward = self.do_the_reroll(n_dices=(action+1))
            self.current_state = Game_Moment.TABELA
            return (self.get_game_state())
            return (self.get_game_state(), self.reward, self.is_ended)
        
        elif game_moment == Game_Moment.TABELA:
            avaiable_cells = list(self.get_empty_cells(state).keys())
            table_index = avaiable_cells[action]
            self.game_play.append("suas opções são:                     " + str(avaiable_cells))
            self.reward = self.set_cell_value(table_index)
            if -1 not in self.desordem.values():
                self.game_play.append("fim do jogo")
                self.current_state = Game_Moment.FIM
                return (self.get_game_state())
                return (self.get_game_state(), self.reward, self.is_ended)
            else:
                self.is_ended = False
                self.current_state = Game_Moment.SECOS_1
                self.dices = self.roll_dice(5)
                self.dices.sort()
                return (self.get_game_state())
                return (self.get_game_state(), self.reward, self.is_ended)
            
        else:
            self.current_state = Game_Moment.FIM
            self.is_ended = True
            return (self.get_game_state())
            return (self.get_game_state(), self.get_total_score(), self.is_ended)
    

    def check_ended(self, state):
        self.set_state(state)
        return -1 not in self.desordem.values()
    
    def get_value_and_terminated(self, state, action):
        if action == None:
            return (0, False)
        self.set_state(state)
        if self.check_ended(state):
            return self.get_total_score(state), self.check_ended(state)
        else:
            return self.reward, self.check_ended(state)
    

    def get_total_score(self, state):
        self.set_state(state)
        self.score_values = list(self.desordem.values())
        self.total = sum(self.score_values)
        total_upper = sum(self.score_values[0:6])
        if total_upper >= 60:
            self.total += 30
        # print()
        self.game_play.append("sua tabela ficou assim:              " + str(self.desordem))
        self.game_play.append("TOTAL:                               " + str(self.total))
        print("total: ", self.total)
        print("sua tabela ficou assim: ", self.desordem)
        print()
        

        return self.total

    

In [4]:
class Node:
    def __init__(self, game, args, state, parent=None, action_taken=None):
        self.game = game
        self.args = args
        self.state = state
        self.parent = parent
        self.action_taken = action_taken
        
        self.children = []
        self.expandable_moves = game.get_valid_moves(state)
        
        self.visit_count = 0
        self.value_sum = 0
        
    def is_fully_expanded(self):
        return np.sum(self.expandable_moves) == 0 and len(self.children) > 0
    
    def select(self):
        best_child = None
        best_ucb = -np.inf
        
        for child in self.children:
            ucb = self.get_ucb(child)
            if ucb > best_ucb:
                best_child = child
                best_ucb = ucb
                
        return best_child
    
    def get_ucb(self, child):
        # normalizar o value_sum
        q_value = (child.value_sum / child.visit_count)
        return q_value + self.args['C'] * math.sqrt(math.log(self.visit_count) / child.visit_count)
    
    def expand(self):
        action = int(np.random.choice(np.where(self.expandable_moves == 1)[0]))
        self.expandable_moves[action] = 0
        
        child_state = self.state.copy()
        child_state = self.game.get_next_state(child_state, action)
        
        child = Node(self.game, self.args, child_state, self, action)
        self.children.append(child)
        return child
    
    def simulate(self):
        value, is_terminal = self.game.get_value_and_terminated(self.state, self.action_taken)
        # value = self.game.get_opponent_value(value)
        
        if is_terminal:
            return value
        
        rollout_state = self.state.copy()
        # rollout_player = 1
        while True:
            valid_moves = self.game.get_valid_moves(rollout_state)
            action = np.random.choice(len(valid_moves))
            rollout_state = self.game.get_next_state(rollout_state, action)
            value, is_terminal = self.game.get_value_and_terminated(rollout_state, action)
            if is_terminal:
                return value    
            
            
    def backpropagate(self, value):
        self.value_sum += value
        self.visit_count += 1
        
        value = self.game.reward
        if self.parent is not None:
            self.parent.backpropagate(value)  


class MCTS:
    def __init__(self, game, args):
        self.game = game
        self.args = args
        
    def search(self, state):
        root = Node(self.game, self.args, state)
        
        for search in range(self.args['num_searches']):
            node = root
            
            while node.is_fully_expanded():
                node = node.select()
                
            value, is_terminal = self.game.get_value_and_terminated(node.state, node.action_taken)
            
            if not is_terminal:
                node = node.expand()
                value = node.simulate()
                
            node.backpropagate(value)    
            
            
        action_probs = self.game.get_valid_moves(state)
        for child in root.children:
            action_probs[child.action_taken] = child.visit_count
        action_probs /= np.sum(action_probs)
        return action_probs
        
        
        

In [6]:
game = Yan()

args = {
    'C': 1.41,
    'num_searches': 10000
}

mcts = MCTS(game, args)

state = game.get_initial_state()


while True:
    print(state)
    
    mcts_probs = mcts.search(state)
    action = np.argmax(mcts_probs)
        
    state = game.get_next_state(state, action)
    
    value, is_terminal = game.get_value_and_terminated(state, action)
    
    if is_terminal:
        print(game.desordem)
        print(game.get_total_score(state))
        game.reset()
        break
        
    # player = game.get_opponent(player)


[<Game_Moment.SECOS_1: 1>, 2, 4, 4, 4, 5, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1]


total:  52
sua tabela ficou assim:  {'1': 0, '2': 0, '3': 9, '4': 4, '5': 0, '6': 0, 'q': 0, 'f': 0, 's+': 0, 's-': 0, 'x+': 21, 'x-': 18, 'y': 0}

total:  17
sua tabela ficou assim:  {'1': 0, '2': 4, '3': 0, '4': 4, '5': 0, '6': 0, 'q': 0, 'f': 0, 's+': 0, 's-': 0, 'x+': 9, 'x-': 0, 'y': 0}

total:  38
sua tabela ficou assim:  {'1': 1, '2': 0, '3': 0, '4': 0, '5': 5, '6': 6, 'q': 0, 'f': 0, 's+': 0, 's-': 0, 'x+': 0, 'x-': 26, 'y': 0}

total:  107
sua tabela ficou assim:  {'1': 0, '2': 4, '3': 3, '4': 4, '5': 0, '6': 0, 'q': 0, 'f': 0, 's+': 60, 's-': 0, 'x+': 19, 'x-': 17, 'y': 0}

total:  49
sua tabela ficou assim:  {'1': 0, '2': 2, '3': 3, '4': 4, '5': 0, '6': 6, 'q': 0, 'f': 0, 's+': 0, 's-': 0, 'x+': 19, 'x-': 15, 'y': 0}

total:  41
sua tabela ficou assim:  {'1': 1, '2': 0, '3': 0, '4': 4, '5': 5, '6': 6, 'q': 0, 'f': 0, 's+': 0, 's-': 0, 'x+': 0, 'x-': 25, 'y': 0}

total:  47
sua tabela ficou assim:  {'1': 1, '2': 2, '3': 3, '4': 4, '5': 5, '6': 12, 'q': 0, 'f': 0, 's+': 0, 's